# Advanced Analytics and Applications
## Analytics Anacondas 

### Visualization

In [45]:
# import relevant libaries 
import pandas as pd
import numpy as np 
import seaborn as sns 
import matplotlib.pyplot as plt 
import glob 
from vincenty import vincenty
import datetime

import geopandas
import json
# conda install h3-py -c conda-forge
from h3 import h3
from shapely.geometry import shape
from descartes import PolygonPatch

import folium

from folium import plugins
from folium.plugins import HeatMapWithTime
from folium.plugins import MarkerCluster
import geopandas as gpd
from shapely.geometry import Point
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.utils import shuffle


from h3 import h3
from shapely.geometry import shape
from descartes import PolygonPatch

# import timeit to measure execution times
import timeit

#imports of folium for map visualization
import folium
from folium import plugins
from folium.plugins import HeatMap

#import Matplotlib Ticker to style axes of figures
import matplotlib.ticker as ticker

import warnings
warnings.filterwarnings(action='ignore')

In [2]:
# read in the availabe data for every month and day 
df = pd.DataFrame()

#read in files for each month 
# for i in range(1,13): 
#     if i <10: 
#         #read in files for each day
#         for i in glob.glob("Data/2019/0" + str(i) +"/*.csv"):     
#             df_1 = pd.read_csv(i, sep=',')
#             df = pd.concat([df, df_1],axis=0)    # concatenate to one dateframe     
#     else: 
#         #read in files for each day
#         for i in glob.glob("Data/2019/" + str(i) +"/*.csv"):     
#             df_1 = pd.read_csv(i, sep=',')
#             df = pd.concat([df, df_1],axis=0)    # concatenate to one dateframe     

# df.reset_index(drop=True,inplace=True)   

df = pd.read_csv("Data/compressedRawData.csv")

In [3]:
df.to_csv("Data/compressedRawData.csv")

#### Availability of bikes

In [4]:
trips = pd.read_csv("Data/bonn_trips.csv",index_col=0)
trips["count"] = 1 
trips = trips[(trips['p_number_start'] != 0) & (trips['p_number_end'] != 0)]
trips_per_station = trips.groupby(["latitude_start", "longitude_start", "p_name_start"]).count()[["count"]]
trips_per_station.reset_index(inplace=True)
trips_per_station.rename(columns={"latitude_start":"latitude", "longitude_start":"longitude", "p_name_start":"p_name"}, inplace=True)
trips_per_station


latitude  longitude                   p_name  count
0    50.661191   7.191865       Mainzer Straße 178      1
1    50.662116   7.184938         Langenbergsweg 8      1
2    50.664601   7.171181         Lannesdorf Mitte    109
3    50.666676   7.169450  Deutschherrenstraße 165      1
4    50.668494   7.181722           Bahnhof Mehlem    191
..         ...        ...                      ...    ...
211  50.755230   7.076526           Pariser Straße    390
212  50.755331   7.076241           Pariser Straße     19
213  50.755938   7.090740          Römerstraße 306      1
214  50.758852   7.047053                Buschdorf    299
215  50.762258   7.055769       Friedlandstraße 70      1

[216 rows x 4 columns]

In [71]:
city_bounding_box = geopandas.read_file('Data/bonnBoundaries.geojson')
city_bounding_box_json_string = city_bounding_box.to_json()
city_bounding_box_json = json.loads(city_bounding_box_json_string)
# 4 Bezirke
city_bounding_box_poly0 = city_bounding_box_json["features"][0]
city_bounding_box_poly1 = city_bounding_box_json["features"][1]
city_bounding_box_poly2 = city_bounding_box_json["features"][2]
city_bounding_box_poly3 = city_bounding_box_json["features"][3]

In [72]:
H3_HEXAGON_RESOLUTION = 9
polygon_obj0 = city_bounding_box_poly0["geometry"] # Bonn Boundaries 
polygon_obj1 = city_bounding_box_poly1["geometry"] # Bonn Boundaries 
polygon_obj2 = city_bounding_box_poly2["geometry"] # Bonn Boundaries 
polygon_obj3 = city_bounding_box_poly3["geometry"] # Bonn Boundaries 


In [81]:
# creating hexagons 
hexagons0 = h3.polyfill(geo_json = polygon_obj0, res = H3_HEXAGON_RESOLUTION, geo_json_conformant = True)
hexagons1 = h3.polyfill(geo_json = polygon_obj1, res = H3_HEXAGON_RESOLUTION, geo_json_conformant = True)
hexagons2 = h3.polyfill(geo_json = polygon_obj2, res = H3_HEXAGON_RESOLUTION, geo_json_conformant = True)
hexagons3 = h3.polyfill(geo_json = polygon_obj3, res = H3_HEXAGON_RESOLUTION, geo_json_conformant = True)

hexagons = hexagons0.union(hexagons1,hexagons2,hexagons3) 

In [82]:
# Convert H3 Indexes to Geometry Objects

# Create geo data frame
df = geopandas.GeoDataFrame(list(hexagons), columns=['h3_hex_id'], crs="EPSG:4326")


In [83]:
# transform h3 to geo_boundary 
df['geometry'] = df[(df['h3_hex_id'].notna())].apply(lambda row: shape({"type": "Polygon",
                                           "coordinates": [h3.h3_to_geo_boundary(h3_address=row["h3_hex_id"], geo_json=True)],
                                           "properties": ""
                                           }), axis=1)


In [86]:
#from folium.plugins import HeatMap
m = folium.Map(location = [50.7323,7.1847], zoom_start=11.2)

HeatMap(data=trips_per_station[["latitude","longitude","count"]],radius=10).add_to(m)

for index, row in df.iterrows(): 
    folium.Choropleth(df.iloc[index].geometry,fill_color='transparent').add_to(m)

folium.Choropleth(
    geo_data="Data/bonnBoundaries.geojson",
    fill_opacity=0.1,
    line_opacity=1,).add_to(m)

m

In [5]:
# delete the "non-stations"
df = df[df['p_number'] != 0]
df.loc[:,'datetime'] = pd.to_datetime(df.loc[:, 'datetime'])

In [6]:
stationlist = df['p_name'].unique()

In [7]:
# Create dataframe with hourly timestamps
df_availableBikes = pd.DataFrame(np.arange('2019-01-20', '2019-12-31', dtype='datetime64[h]'), columns = ['time'])

In [8]:
df_availableBikes['time'] = df_availableBikes['time'].dt.strftime('%Y-%m-%d-%H')
df_availableBikes

time
0     2019-01-20-00
1     2019-01-20-01
2     2019-01-20-02
3     2019-01-20-03
4     2019-01-20-04
...             ...
8275  2019-12-30-19
8276  2019-12-30-20
8277  2019-12-30-21
8278  2019-12-30-22
8279  2019-12-30-23

[8280 rows x 1 columns]

In [9]:
for station in stationlist: 
    df_availableBikes[station] = np.NaN

In [10]:
df_availableBikes.head()

time  Hans-Steger-Ufer  Bahnhof Oberkassel  Schauspielhalle  \
0  2019-01-20-00               NaN                 NaN              NaN   
1  2019-01-20-01               NaN                 NaN              NaN   
2  2019-01-20-02               NaN                 NaN              NaN   
3  2019-01-20-03               NaN                 NaN              NaN   
4  2019-01-20-04               NaN                 NaN              NaN   

   Malteser Krankenhaus  Alter Friedhof  Juridicum  Nassestr./Riesstr.  \
0                   NaN             NaN        NaN                 NaN   
1                   NaN             NaN        NaN                 NaN   
2                   NaN             NaN        NaN                 NaN   
3                   NaN             NaN        NaN                 NaN   
4                   NaN             NaN        NaN                 NaN   

   Theater Bonn  Bonn Information  ...  Telemannstraße 22  Karl-Duwe-Straße  \
0           NaN               NaN  ...                NaN               NaN   
1           NaN               NaN  ...                NaN               NaN   
2           NaN               NaN  ...                NaN               NaN   
3           NaN               NaN  ...                NaN               NaN   
4           NaN               NaN  ...                NaN               NaN   

   BIKE 45265  BIKE 45329  Prinz-Albert-Straße 29  BIKE 45298  \
0         NaN         NaN                     NaN         NaN   
1         NaN         NaN                     NaN         NaN   
2         NaN         NaN                     NaN         NaN   
3         NaN         NaN                     NaN         NaN   
4         NaN         NaN                     NaN         NaN   

   Konrad-Adenauer-Platz  Bonner Bogen  Haltepunkt Plittersdorfer Straße  \
0                    NaN           NaN                               NaN   
1                    NaN           NaN                               NaN   
2                    NaN           NaN                               NaN   
3                    NaN           NaN                               NaN   
4                    NaN           NaN                               NaN   

   Poppelsdorfer Platz  
0                  NaN  
1                  NaN  
2                  NaN  
3                  NaN  
4                  NaN  

[5 rows x 290 columns]

In [11]:
df_availableBikes = df_availableBikes.set_index('time')

In [12]:
# get the amount of available bikes at each station for different timestamps
for index, row in df.iterrows():
    timestamp = pd.to_datetime(row.get(key = 'datetime')).ceil('H').strftime('%Y-%m-%d-%H')
    df_availableBikes.at[timestamp, row.get(key = 'p_name')] = pd.to_numeric(row.get(key = 'p_bikes'))

In [13]:
df_availableBikes.fillna(method='ffill', inplace=True)
df_availableBikes.fillna(value='0.0', inplace=True)
df_availableBikes

Hans-Steger-Ufer Bahnhof Oberkassel  Schauspielhalle  \
time                                                                  
2019-01-20-00               1.0                0.0              1.0   
2019-01-20-01               1.0                0.0              1.0   
2019-01-20-02               1.0                0.0              1.0   
2019-01-20-03               1.0                0.0              1.0   
2019-01-20-04               1.0                0.0              1.0   
...                         ...                ...              ...   
2019-12-31-07               1.0                  1              1.0   
2019-12-31-23               1.0                  1              1.0   
2019-12-31-04               1.0                  1              1.0   
2019-12-31-08               1.0                  1              1.0   
2019-12-31-01               1.0                  1              1.0   

               Malteser Krankenhaus  Alter Friedhof Juridicum  \
time                                                            
2019-01-20-00                   3.0             1.0       0.0   
2019-01-20-01                   3.0             1.0       0.0   
2019-01-20-02                   3.0             1.0       0.0   
2019-01-20-03                   3.0             1.0       0.0   
2019-01-20-04                   3.0             2.0       0.0   
...                             ...             ...       ...   
2019-12-31-07                   1.0             1.0         1   
2019-12-31-23                   1.0             1.0         1   
2019-12-31-04                   1.0             1.0         1   
2019-12-31-08                   1.0             1.0         1   
2019-12-31-01                   1.0             1.0         1   

               Nassestr./Riesstr.  Theater Bonn Bonn Information UN-Campus  \
time                                                                         
2019-01-20-00                 3.0           1.0              0.0       0.0   
2019-01-20-01                 3.0           1.0              0.0       0.0   
2019-01-20-02                 3.0           2.0              0.0       0.0   
2019-01-20-03                 3.0           2.0              0.0       0.0   
2019-01-20-04                 3.0           2.0              0.0       0.0   
...                           ...           ...              ...       ...   
2019-12-31-07                 1.0           1.0                1         3   
2019-12-31-23                 1.0           1.0                1         1   
2019-12-31-04                 1.0           1.0                1         1   
2019-12-31-08                 1.0           1.0                1         1   
2019-12-31-01                 1.0           1.0                1         1   

               ... Telemannstraße 22  Karl-Duwe-Straße  BIKE 45265  \
time           ...                                                   
2019-01-20-00  ...               0.0               0.0         0.0   
2019-01-20-01  ...               0.0               0.0         0.0   
2019-01-20-02  ...               0.0               0.0         0.0   
2019-01-20-03  ...               0.0               0.0         0.0   
2019-01-20-04  ...               0.0               0.0         0.0   
...            ...               ...               ...         ...   
2019-12-31-07  ...                 1                 1           1   
2019-12-31-23  ...                 1                 1           1   
2019-12-31-04  ...                 1                 1           1   
2019-12-31-08  ...                 1                 1           1   
2019-12-31-01  ...                 1                 1           1   

               BIKE 45329  Prinz-Albert-Straße 29  BIKE 45298  \
time                                                            
2019-01-20-00         0.0                     0.0         0.0   
2019-01-20-01         0.0                     0.0         0.0   
2019-01-20-02         0.0                     0.0         0

In [14]:
data = pd.DataFrame(df_availableBikes.loc['2019-12-31-11'])

In [15]:
data.reset_index(inplace=True)
data = data.rename(columns={'index': 'p_name', '2019-12-31-11':'NumberOfBikes'})
data

p_name NumberOfBikes
0                    Hans-Steger-Ufer             1
1                  Bahnhof Oberkassel             1
2                     Schauspielhalle             1
3                Malteser Krankenhaus             1
4                      Alter Friedhof             1
..                                ...           ...
284                        BIKE 45298             1
285             Konrad-Adenauer-Platz             1
286                      Bonner Bogen             1
287  Haltepunkt Plittersdorfer Straße             1
288               Poppelsdorfer Platz             1

[289 rows x 2 columns]

In [16]:
data

p_name NumberOfBikes
0                    Hans-Steger-Ufer             1
1                  Bahnhof Oberkassel             1
2                     Schauspielhalle             1
3                Malteser Krankenhaus             1
4                      Alter Friedhof             1
..                                ...           ...
284                        BIKE 45298             1
285             Konrad-Adenauer-Platz             1
286                      Bonner Bogen             1
287  Haltepunkt Plittersdorfer Straße             1
288               Poppelsdorfer Platz             1

[289 rows x 2 columns]

In [17]:
bikenumber_one_moment = pd.merge(data, trips_per_station, on="p_name")


In [91]:
m = folium.Map(location = [50.7323,7.1847], zoom_start=11, min_zoom=10.5, max_zoom=16)

# draw the borders of Bonn and its districts
folium.Choropleth(
    geo_data="Data/bonnBoundaries.geojson", 
    fill_color = 'grey',
    fill_opacity=0.4,
    ).add_to(m)

for index, row in df.iterrows(): 
    folium.Choropleth(df.iloc[index].geometry,fill_color='transparent').add_to(m)

for index, row in bikenumber_one_moment.iterrows():
    bikenumber = int(row['NumberOfBikes'])
    station_name = row['p_name']    
    station_info = "Name: {}\n\nAvailable bikes: {}\n".format(station_name,bikenumber)    
  
    folium.Circle(
      location=[row['latitude'],row['longitude']],
      popup=station_info,
      radius=row['NumberOfBikes']*30,
      color='red',
      fill=True,
      fill_color='#red'
    ).add_to(m) 

m